In [3]:
"""
Multi-Agent Dynamic Grid World Environment
Created by: Ardianto Wibowo
"""

import numpy as np
import sys

# Add the path to the 'env' folder to sys.path
sys.path.append('env')

from ma_gridworld import Env

class SearchAgent:
    def __init__(self, num_actions):
        self.num_actions = num_actions
        self.targets_seen = []
        
    def analyse_sensor_data(self, agent_id, coordinate_observation, sensor_data_observation):
        for i in range(len(sensor_data_observation)):
            for j in range(len(sensor_data_observation[i])):
                data = sensor_data_observation[i][j]
                location = [coordinate_observation[0] + j - len(sensor_data_observation[i])//2,
                           coordinate_observation[1] + i - len(sensor_data_observation)//2]
                if data != None and 'target_' + str(agent_id) in data:
                    if location not in self.targets_seen:
                        self.targets_seen.append(location)
                # Remove collected targets from targets_seen
                if location[0] == coordinate_observation[0] and location[1] == coordinate_observation[1]:
                    if location in self.targets_seen:
                        self.targets_seen.remove(location)
        
    def analyse_communication(self, agent_id, comm_observation):
        for comm in comm_observation:
            origin_location = comm[0]
            sensor_data_observation = comm[1]
            for i in range(len(sensor_data_observation)):
                for j in range(len(sensor_data_observation[i])):
                    data = sensor_data_observation[i][j]
                    location = [origin_location[0] + j - len(sensor_data_observation[i])//2,
                               origin_location[1] + i - len(sensor_data_observation)//2]
                    if data != None and 'target_' + str(agent_id) in data:
                        if location not in self.targets_seen:
                            self.targets_seen.append(location)

    def select_action(self, coordinate_observation):
        if len(self.targets_seen) > 0:
            # find the closest target
            closest_target = None
            closest_target_distance = 999999
            for target_coordinate in self.targets_seen:
                horizontal_distance = target_coordinate[0] - coordinate_observation[0]
                vertical_distance = target_coordinate[1] - coordinate_observation[1]
                distance = abs(horizontal_distance) + abs(vertical_distance)
                if distance < closest_target_distance:
                    closest_target_distance = distance
                    closest_target = target_coordinate
            horizontal_distance = closest_target[0] - coordinate_observation[0]
            vertical_distance = closest_target[1] - coordinate_observation[1]
            if abs(horizontal_distance) >= abs(vertical_distance):
                if horizontal_distance < 0:
                    return 3
                elif horizontal_distance > 0:
                    return 4
                return 0
            else:
                if vertical_distance < 0:
                    return 1
                elif vertical_distance > 0:
                    return 2
                return 0
        else:
            return np.random.choice(num_actions-1) + 1 # example of random value as a physical action


def get_action(agent_id, observation, num_actions, agents, env):
    """
    This method provide a random action chosen recognized by the ma-gridworld environment:
    1: up, 2: down, 3: left, 4: right, 0: stay
    """
    
    coordinate_observation = tuple(observation[0])  # Keep observation as (x, y) tuple

    #optional observation data may be used, depend on the agent needs.
    win_state_observation = observation[1]
    sensor_data_observation = observation[2]
    comm_observation = observation[3]

    agents[agent_id].analyse_sensor_data(agent_id, coordinate_observation, sensor_data_observation)
    agents[agent_id].analyse_communication(agent_id, comm_observation)
    physical_action = agents[agent_id].select_action(coordinate_observation)

    if env.is_agent_silent:
        comm_action = [] # communication action is set to be zero if agent silent
    else:
        comm_action = [coordinate_observation, sensor_data_observation] # example of random value as a communication action
    
    return (physical_action, comm_action)


def run(num_episodes, max_steps_per_episode, agents, num_actions, env):
    for episode in range(num_episodes):
        print(f"Starting episode {episode + 1}")
        observations = env.reset()  # Reset the environment at the start of each episode
        
        for agent in agents:
            agent.__init__(num_actions)
        
        done = [False] * env.num_agents  # Initialize 'done' as a list for each agent
        step_count = 0

        while not all(done) and step_count < max_steps_per_episode:  # Stop if all agents are done or max steps reached
            actions = []
            next_observations = []
            
            for agent_id in range(env.num_agents):
                observation = observations[agent_id]
                action = get_action(agent_id, observation, num_actions, agents, env)
                
                actions.append(action)
                next_observations.append(observation)

            next_observations, rewards, done = env.step(actions)  # Step in the environment

            observations = next_observations
            step_count += 1

            # Render the environment
            env.render()

            print(f"Step {step_count}:")
            for agent_id in range(env.num_agents):
                print(f"  Agent {agent_id}: Observation: {observations}, Action: {actions[agent_id]}, Reward: {rewards[agent_id]}, Done: {done[agent_id]}")

        print(f"Episode {episode + 1} finished after {step_count} steps.\n")


if __name__ == "__main__":

    gsize=15 #grid size (square)
    gpixels=30 #grid cell size in pixels

    is_sensor_active = True #True:  Activate the sensory observation data
    sensory_size = 3 #'is_sensor_active' must be True. The value must be odd, if event will be converted to one level odd number above
    
    num_agents = 10 #the number of agents will be run in paralel
    num_obstacles = 0 #the number of obstacles
    is_single_target = False #True: all agents have a single target, False: each agent has their own target
    num_targets_per_agent = 5 #'is_single_target' must be true to have an effect
    
    is_agent_silent = True #True: communication among agents is allowed

    num_episodes=1 #the number of episode will be run
    max_steps_per_episode=500 #each episode will be stopped when max_step is reached

    eps_moving_targets = 10 #set this value greater than 'num_episodes' to keep the targets in a stationary position
    eps_moving_obstacles = 10 #set this value greater than 'num_episodes' to keep the obstacles in a stationary position

    render = True #True: render the animation into the screen (so far, it is still can not be deactivated)

    min_obstacle_distance_from_target = 1 #min grid distance of each obstacles relative to targets
    max_obstacle_distance_from_target = 5 #max grid distance of each obstacles relative to targets
    min_obstacle_distance_from_agents = 1 #min grid distance of each obstacles relative to agents

    reward_normal = -1 #reward value of normal steps
    reward_obstacle = -5 #reward value when hit an obstacle
    reward_target = 50 #reward value when reach the target

    is_totally_random = True #True: target and obstacles initial as well as movement position is always random on each call, False: only random at the beginning. 
    animation_speed = 0.1 #smaller is faster 
    is_destroy_environment = True #True: automatically close the animation after all episodes end.  

    # Initialize environment
    env = Env(
        num_agents=num_agents, num_targets_per_agent=num_targets_per_agent, num_obstacles=num_obstacles,
        eps_moving_obstacles=eps_moving_obstacles, eps_moving_targets=eps_moving_targets,
        is_agent_silent=is_agent_silent, is_single_target=is_single_target, sensory_size=sensory_size,
        gpixels=gpixels, gheight=gsize, gwidth=gsize, is_sensor_active=is_sensor_active,
        min_obstacle_distance_from_target=min_obstacle_distance_from_target,
        max_obstacle_distance_from_target=max_obstacle_distance_from_target,
        min_obstacle_distance_from_agents=min_obstacle_distance_from_agents,
        is_totally_random=is_totally_random, animation_speed=animation_speed,
        reward_normal=reward_normal, reward_obstacle=reward_obstacle, reward_target=reward_target
    )
    
    num_actions = len(env.action_space)
    
    # Initialize Q-learning agents
    agents = [SearchAgent(num_actions) for _ in range(num_agents)]

    # Run episodes
    run(num_episodes, max_steps_per_episode, agents, num_actions, env)

    if is_destroy_environment:
        env.destroy_environment() 


Starting episode 1
Step 1:
  Agent 0: Observation: [[[1, 0], False, [[None, None, None], ['agent', 'empty', 'empty'], ['empty', 'empty', 'target_5_3']], []], [[14, 1], False, [['empty', 'agent', None], ['empty', 'empty', None], ['empty', 'empty', None]], []], [[14, 14], False, [['empty', 'empty', None], ['empty', 'agent', None], [None, None, None]], []], [[0, 14], False, [[None, 'empty', 'target_7_2'], [None, 'agent', 'empty'], [None, None, None]], []], [[5, 1], False, [['empty', 'agent', 'empty'], ['empty', 'empty', 'target_3_4'], ['empty', 'empty', 'empty']], []], [[9, 0], False, [[None, None, None], ['empty', 'agent', 'empty'], ['empty', 'target_0_0', 'empty']], []], [[14, 5], False, [['empty', 'empty', None], ['target_7_3', 'agent', None], ['empty', 'empty', None]], []], [[14, 8], False, [['target_0_3', 'empty', None], ['empty', 'empty', None], ['target_8_0', 'agent', None]], []], [[7, 13], False, [['empty', 'empty', 'empty'], ['empty', 'empty', 'empty'], ['empty', 'agent', 'empty'

Step 3:
  Agent 0: Observation: [[[0, 0], False, [[None, None, None], [None, 'empty', 'agent'], [None, 'empty', 'empty']], []], [[13, 0], False, [[None, None, None], ['empty', 'empty', 'agent'], ['empty', 'empty', 'empty']], []], [[13, 14], False, [['empty', 'empty', 'empty'], ['empty', 'empty', 'agent'], [None, None, None]], []], [[0, 14], False, [[None, 'empty', 'target_7_2'], [None, 'agent', 'empty'], [None, None, None]], []], [[6, 0], False, [[None, None, None], ['agent', 'empty', 'empty'], ['empty', 'target_3_4', 'empty']], []], [[10, 0], False, [[None, None, None], ['empty', 'agent', 'empty'], ['target_0_0', 'empty', 'empty']], []], [[12, 5], False, [['empty', 'empty', 'empty'], ['target_1_4', 'target_4_3', 'agent'], ['empty', 'empty', 'empty']], []], [[13, 9], False, [['empty', 'empty', 'empty'], ['target_3_2', 'target_8_0', 'agent'], ['empty', 'empty', 'empty']], []], [[8, 14], False, [['empty', 'empty', 'target_4_2'], ['agent', 'empty', 'empty'], [None, None, None]], []], [[0,

Step 5:
  Agent 0: Observation: [[[0, 0], False, [[None, None, None], [None, 'agent', 'empty'], [None, 'empty', 'empty']], []], [[13, 0], False, [[None, None, None], ['agent', 'empty', 'empty'], ['empty', 'empty', 'empty']], []], [[12, 14], False, [['empty', 'empty', 'empty'], ['empty', 'empty', 'agent'], [None, None, None]], []], [[0, 14], False, [[None, 'empty', 'target_7_2'], [None, 'agent', 'empty'], [None, None, None]], []], [[6, 0], False, [[None, None, None], ['agent', 'empty', 'empty'], ['empty', 'target_3_4', 'empty']], []], [[9, 1], False, [['empty', 'empty', 'empty'], ['empty', 'target_0_0', 'agent'], ['empty', 'target_1_0', 'target_9_0']], []], [[13, 6], False, [['target_4_3', 'agent', 'empty'], ['empty', 'empty', 'empty'], ['empty', 'target_0_3', 'empty']], []], [[13, 11], False, [['empty', 'agent', 'empty'], ['target_7_1', 'empty', 'empty'], ['target_3_3', 'target_0_2', 'empty']], []], [[8, 14], False, [['empty', 'agent', 'target_4_2'], ['empty', 'empty', 'empty'], [None,

Step 7:
  Agent 0: Observation: [[[0, 0], False, [[None, None, None], [None, 'agent', 'empty'], [None, 'empty', 'empty']], []], [[14, 1], False, [['empty', 'empty', None], ['agent', 'empty', None], ['empty', 'empty', None]], []], [[12, 14], False, [['empty', 'empty', 'empty'], ['empty', 'empty', 'agent'], [None, None, None]], []], [[0, 14], False, [[None, 'agent', 'target_7_1'], [None, 'empty', 'empty'], [None, None, None]], []], [[7, 1], False, [['empty', 'empty', 'empty'], ['agent', 'empty', 'empty'], ['empty', 'target_8_3', 'empty']], []], [[10, 2], False, [['target_0_0', 'agent', 'empty'], ['target_1_0', 'target_9_0', 'empty'], ['empty', 'empty', 'target_6_2']], []], [[14, 5], False, [['empty', 'empty', None], ['target_7_2', 'empty', None], ['empty', 'agent', None]], []], [[11, 11], False, [['empty', 'target_4_0', 'empty'], ['empty', 'target_9_1', 'agent'], ['empty', 'empty', 'target_3_3']], []], [[8, 12], False, [['target_5_1', 'empty', 'empty'], ['empty', 'empty', 'empty'], ['emp

Step 9:
  Agent 0: Observation: [[[0, 0], False, [[None, None, None], [None, 'agent', 'empty'], [None, 'empty', 'empty']], []], [[14, 0], False, [[None, None, None], ['empty', 'agent', None], ['empty', 'empty', None]], []], [[14, 14], False, [['empty', 'empty', None], ['agent', 'empty', None], [None, None, None]], []], [[0, 12], False, [[None, 'empty', 'target_9_4'], [None, 'empty', 'empty'], [None, 'agent', 'target_7_1']], []], [[8, 2], False, [['empty', 'agent', 'target_0_0'], ['target_8_3', 'empty', 'target_1_0'], ['empty', 'empty', 'empty']], []], [[11, 3], False, [['target_9_0', 'empty', 'target_2_3'], ['agent', 'target_6_2', 'empty'], ['empty', 'empty', 'empty']], []], [[14, 5], False, [['empty', 'agent', None], ['target_7_2', 'empty', None], ['empty', 'empty', None]], []], [[11, 11], False, [['empty', 'target_4_0', 'empty'], ['empty', 'target_9_1', 'agent'], ['empty', 'empty', 'target_3_3']], []], [[8, 12], False, [['target_5_1', 'agent', 'empty'], ['empty', 'empty', 'empty'], [

...

Step 491:
  Agent 0: Observation: [[[6, 11], False, [['empty', 'empty', 'agent'], ['empty', 'empty', 'agent'], ['empty', 'empty', 'empty']], []], [[10, 0], False, [[None, None, None], ['empty', 'empty', 'agent'], ['empty', 'empty', 'empty']], []], [[3, 2], False, [['empty', 'agent', 'empty'], ['empty', 'empty', 'empty'], ['empty', 'empty', 'empty']], []], [[13, 5], False, [['empty', 'empty', 'empty'], ['empty', 'agent', 'agent'], ['empty', 'empty', 'empty']], []], [[8, 4], False, [['empty', 'empty', 'empty'], ['empty', 'empty', 'agent'], ['empty', 'empty', 'agent']], []], [[9, 4], False, [['empty', 'empty', 'empty'], ['agent', 'empty', 'empty'], ['empty', 'agent', 'empty']], []], [[7, 11], False, [['empty', 'agent', 'empty'], ['agent', 'empty', 'empty'], ['empty', 'empty', 'empty']], []], [[0, 4], False, [[None, 'agent', 'empty'], [None, 'empty', 'target_0_0'], [None, 'empty', 'empty']], []], [[12, 5], False, [['empty', 'empty', 'empty'], ['empty', 'empty', 'agent'], ['empty', 'empty',

Step 493:
  Agent 0: Observation: [[[6, 11], False, [['empty', 'empty', 'empty'], ['empty', 'empty', 'empty'], ['empty', 'agent', 'empty']], []], [[9, 1], False, [['empty', 'empty', 'empty'], ['empty', 'empty', 'agent'], ['empty', 'empty', 'empty']], []], [[1, 2], False, [['empty', 'empty', 'empty'], ['empty', 'empty', 'agent'], ['empty', 'empty', 'empty']], []], [[13, 5], False, [['empty', 'empty', 'empty'], ['empty', 'agent', 'empty'], ['empty', 'agent', 'empty']], []], [[10, 4], False, [['empty', 'empty', 'empty'], ['agent', 'empty', 'empty'], ['agent', 'empty', 'empty']], []], [[10, 5], False, [['empty', 'agent', 'empty'], ['agent', 'empty', 'empty'], ['empty', 'empty', 'empty']], []], [[8, 12], False, [['empty', 'agent', 'empty'], ['empty', 'empty', 'empty'], ['empty', 'empty', 'target_4_0']], []], [[1, 3], False, [['empty', 'agent', 'empty'], ['empty', 'empty', 'empty'], ['empty', 'agent', 'empty']], []], [[14, 5], False, [['empty', 'empty', None], ['agent', 'empty', None], ['emp

Step 495:
  Agent 0: Observation: [[[5, 12], False, [['empty', 'agent', 'empty'], ['empty', 'empty', 'empty'], ['empty', 'target_1_0', 'empty']], []], [[9, 1], False, [['empty', 'empty', 'empty'], ['empty', 'empty', 'agent'], ['empty', 'empty', 'empty']], []], [[0, 1], False, [[None, 'empty', 'empty'], [None, 'empty', 'agent'], [None, 'empty', 'empty']], []], [[14, 6], False, [['empty', 'agent', None], ['empty', 'empty', None], ['empty', 'empty', None]], []], [[9, 3], False, [['empty', 'empty', 'empty'], ['empty', 'empty', 'empty'], ['empty', 'agent', 'empty']], []], [[11, 4], False, [['empty', 'empty', 'empty'], ['empty', 'empty', 'empty'], ['empty', 'agent', 'empty']], []], [[8, 12], False, [['empty', 'empty', 'empty'], ['empty', 'empty', 'agent'], ['empty', 'empty', 'target_4_0']], []], [[0, 3], False, [[None, 'empty', 'empty'], [None, 'agent', 'empty'], [None, 'empty', 'target_0_0']], []], [[14, 4], False, [['empty', 'empty', None], ['empty', 'agent', None], ['empty', 'empty', None

Step 497:
  Agent 0: Observation: [[[4, 11], False, [['empty', 'empty', 'empty'], ['empty', 'empty', 'agent'], ['empty', 'empty', 'empty']], []], [[8, 2], False, [['empty', 'agent', 'empty'], ['target_8_0', 'empty', 'empty'], ['empty', 'agent', 'empty']], []], [[1, 2], False, [['empty', 'agent', 'empty'], ['empty', 'empty', 'empty'], ['agent', 'empty', 'empty']], []], [[14, 5], False, [['agent', 'empty', None], ['empty', 'agent', None], ['empty', 'empty', None]], []], [[7, 3], False, [['empty', 'target_8_0', 'agent'], ['empty', 'empty', 'agent'], ['empty', 'empty', 'empty']], []], [[10, 3], False, [['empty', 'empty', 'empty'], ['empty', 'empty', 'agent'], ['empty', 'empty', 'empty']], []], [[8, 12], False, [['empty', 'empty', 'empty'], ['agent', 'empty', 'empty'], ['empty', 'empty', 'target_4_0']], []], [[0, 4], False, [[None, 'agent', 'empty'], [None, 'empty', 'target_0_0'], [None, 'empty', 'empty']], []], [[12, 4], False, [['empty', 'empty', 'empty'], ['empty', 'empty', 'agent'], ['e

Step 499:
  Agent 0: Observation: [[[4, 11], False, [['empty', 'agent', 'empty'], ['empty', 'empty', 'empty'], ['empty', 'empty', 'empty']], []], [[7, 3], False, [['empty', 'target_8_0', 'empty'], ['agent', 'empty', 'agent'], ['empty', 'empty', 'empty']], []], [[2, 1], False, [['empty', 'empty', 'empty'], ['empty', 'empty', 'empty'], ['empty', 'agent', 'empty']], []], [[14, 4], False, [['empty', 'empty', None], ['agent', 'agent', None], ['empty', 'empty', None]], []], [[7, 3], False, [['empty', 'target_8_0', 'empty'], ['agent', 'agent', 'empty'], ['empty', 'empty', 'empty']], []], [[11, 2], False, [['empty', 'empty', 'empty'], ['agent', 'empty', 'empty'], ['empty', 'empty', 'empty']], []], [[8, 12], False, [['empty', 'agent', 'empty'], ['empty', 'empty', 'empty'], ['empty', 'empty', 'target_4_0']], []], [[1, 4], False, [['empty', 'empty', 'empty'], ['agent', 'target_0_0', 'empty'], ['empty', 'empty', 'empty']], []], [[13, 3], False, [['empty', 'empty', 'empty'], ['empty', 'empty', 'emp